In [1]:
import numpy as np
import matplotlib.pyplot as plt
from skimage import io
from skimage import img_as_ubyte, img_as_uint, img_as_float64
from skimage.transform import rotate
from matplotlib.animation import FFMpegWriter
import glob

In [2]:
def PrintArrayInfo(a):
    print("Array info:")
    print("shape:", a.shape)
    print("dtype:", a.dtype)
    print("min, max:", a.min(), a.max())
    print()

In [3]:
# Calculating initial November image for Zoom-In
NIR   = io.imread('Downloads/Band5/11_band5.tif')
NIR   = img_as_float64(NIR)

Red   = io.imread('Downloads/Band4/11_band4.tif')
Red   = img_as_float64(Red)

# 3, Initializing necessary arrays
nx,ny      = NIR.shape
NDVI       = np.zeros([nx,ny],dtype = np.float64)
NDVI_num   = np.zeros([nx,ny],dtype = np.float64)
NDVI_den   = np.zeros([nx,ny],dtype = np.float64)


# 4, Preliminary equations, numerator and denominator
NDVI_num = NIR - Red
NDVI_den = NIR + Red

#5, Putting together NDVI Calculation
Min = -1
Max = +1

for i in range(nx):
    for j in range(ny):
        if (NDVI_den[i,j] != 0):
            NDVI[i,j] =  NDVI_num[i,j] / NDVI_den[i,j]
        else:
            NDVI[i,j] = 0
        if (NDVI[i,j] < Min):
            NDVI[i,j] = Min
        if (NDVI[i,j] > Max):
            NDVI[i,j] = Max


#5, Rescaling the image 
Rescale = np.copy(NDVI)
Rescale = ((Rescale - Rescale.min()) / 
           (Rescale.max() - Rescale.min()))


# 6, Rotating image
Rot = rotate(Rescale,13.5)

# 7, Cropping image

Crop  = Rot[1000:6750,2000:6900]
NDVI_Nov = np.copy(Crop)

In [4]:
PrintArrayInfo(NDVI_Nov)

Array info:
shape: (5750, 4900)
dtype: float64
min, max: 0.0004425130490696527 1.0



In [5]:
# plt.imshow(NDVI_Nov, cmap = 'RdYlGn')
# plt.show()

In [6]:
nx, ny = NDVI_Nov.shape

In [7]:
%matplotlib osx
%config InlineBackend.figure_format = 'retina'
from matplotlib.animation import FFMpegWriter
metadata = dict(title='Zoom', artist='NonnieCoelho',comment='Zoooom')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)

fig = plt.figure(dpi=200)

# Initializing Center Value to zoom into
Cent_x = np.int((.4*nx))
Cent_y = np.int((.6*ny))

xl = Cent_x
xL = np.int(nx - Cent_x)
yl = Cent_y
yL = np.int(ny - Cent_y)




delta = np.linspace(1,0,101)


with writer.saving(fig, "Zoom_Final3.mp4", dpi=200):  
    Step    = 0
    StepMax = (.65*len(delta)) // 1
    while (Step < StepMax):
        xmin = np.int(Cent_x - delta[Step]*xl)
        xmax = np.int(Cent_x + delta[Step]*xL)
        ymin = np.int(Cent_y - delta[Step]*yl)
        ymax = np.int(Cent_y + delta[Step]*yL)
        Zoom = NDVI_Nov[xmin:xmax,ymin:ymax]


        # 9, PLOTTING, MP4 FRAMES
        plt.rcParams['figure.figsize'] = [20, 20]
        plt.axis('off')
        plt.imshow(Zoom, cmap = 'RdYlGn')
        plt.title('After Kincade fire: November 2019', fontsize = 20)
        # plt.colorbar()
        plt.pause(1.0)
        
        
        Step += 1
        writer.grab_frame()
        # plt.clf()
